In [24]:
!pip install rapidfuzz

In [28]:
import pandas as pd
from rapidfuzz import fuzz, process
from collections import defaultdict

In [32]:
# Replace with your filtered CSV file path
input_file = "/home/nikhikhas/TradeSweep/datasets/panjiva_us_imports_02_2015_filtered_HSCode.csv"

df = pd.read_csv(input_file)
df.head()
#df.columns

PanjivaRecordID BillOfLadingNumber ArrivalDate DataLoadDate DataLaunchDate  \
0        107625726    MOLU11032251740  2015-02-03   2015-02-04     2015-02-06   
1        107753726    ASTI75524127999  2015-02-08   2015-02-09     2015-02-11   
2        107686654     COSU6107751810  2015-02-04   2015-02-05     2015-02-07   
3        107662654     YMLUW234009404  2015-02-01   2015-02-03     2015-02-05   
4        107644350      OWLQHK1400485  2015-02-03   2015-02-04     2015-02-06   

         ConsigneeName                            ConsigneeFullAddress  \
0         Haworth Inc.     316 HIGHWAY 9 S BRUCE MISSISSIPPI 389159781   
1     Republic Tobacco           2301 RAVINE WAY GLENVIEW IL 60025 USA   
2  Fulton Seafood Inc.            2818 MCKINNEY ST HOUSTON TEXAS 77003   
3      Elegant Windows  3709 EAST RANDOL MILL ROAD ARLINGTON, TX 76011   
4         Quirch Foods                        7600 NW 82ND PLACE MIAMI   

          ConsigneeRoute ConsigneeCity ConsigneeStateRegion  ... HasLCL  \
0              Highway 9         Bruce          Mississippi  ...    NaN   
1        2301 Ravine Way      Glenview             Illinois  ...    NaN   
2   2818 McKinney Street       Houston                Texas  ...    NaN   
3  3709 E Randol Mill Rd     Arlington                Texas  ...    NaN   
4                    NaN           NaN                  NaN  ...    NaN   

  ContainerNumbers   HSCode  \
0      MOEU1409807  0391733   
1      TGHU4143476  0320300   
2      CBHU2817521   030323   
3      YMLU3264973  0392112   
4      SEGU9052257   030461   

                                        GoodsShipped  VolumeContainerTEU  \
0  168  CTN CHAIR PARTS ARM ASSY,HEIGHT ADJ,TR_F ...                 0.4   
1                                      COLOR BOX . .                 2.0   
2                   FROZEN GUTTED AND SCALED TILAPIA                 2.0   
3  PLATES  SHEETS  ETC    STRIP  CELL  PLYM VINY ...                 1.0   
4   FROZEN TILAPIA FILLETS PO NO. 394814 HS CODE IUS                 2.0   

                                      ContainerMarks DividedLCL  \
0  168  CTN CHAIR PARTS ARM ASSY,HEIGHT ADJ,TR_F ...          Y   
1  R T L.P 2301 RAVINE WAY GLENVIEW ,IL 60025 IT ...          N   
2                                                NaN          N   
3  A.F.P. (IN DIA.) WHITTIER,CA PO028081-00 CTN1-...          N   
4        030461 CONTAINER IS SET AT -18 DEGREES CELS          N   

  ContainerTypeOfService ContainerTypes DangerousGoods  
0         House to House           9500          false  
1           Pier to Pier            NaN          false  
2         House to House           4532          false  
3         House to House           22G0          false  
4           Pier to Pier            NaN          false  

[5 rows x 77 columns]

In [36]:
# Columns to cluster and their ID anchors
name_columns = {
    "ConsigneeName": ["ConsigneeLocalDUNS", "ConsigneePanjivaID"],
    "ShipperName": ["ShipperPanjivaID"]
}

# Fuzzy matching threshold (0-100)
similarity_threshold = 85


In [40]:
def cluster_names(df, name_col, id_cols):
    """
    Cluster similar names using fuzzy matching and IDs.
    Returns a dict: {canonical_name: [all_names_in_cluster]}
    """
    # Group by IDs first to anchor similar entities
    id_groups = df.groupby(id_cols)
    clusters = {}

    for _, group in id_groups:
        names = group[name_col].dropna().unique().tolist()
        if not names:
            continue

        # Start clustering
        cluster_list = []
        while names:
            base_name = names.pop(0)
            current_cluster = [base_name]

            matches_to_remove = []
            for other_name in names:
                score = fuzz.token_sort_ratio(base_name, other_name)
                if score >= similarity_threshold:
                    current_cluster.append(other_name)
                    matches_to_remove.append(other_name)

            # Remove matched names from names list
            for name_rm in matches_to_remove:
                names.remove(name_rm)

            # Decide canonical name (choose the longest one or first)
            canonical_name = max(current_cluster, key=len)
            clusters[canonical_name] = current_cluster

    return clusters


In [44]:
all_clusters = {}

for name_col, id_cols in name_columns.items():
    clusters = cluster_names(df, name_col, id_cols)
    all_clusters[name_col] = clusters
    
for name_col, clusters in all_clusters.items():
    print(f"\nClusters for {name_col}:")
    for canonical, group in clusters.items():
        print(f"Canonical: {canonical}")
        print(f"Group: {group}\n")

for name_col, clusters in all_clusters.items():
    rows = []
    for canonical, group in clusters.items():
        for name in group:
            rows.append({"CanonicalName": canonical, "Name": name})
    out_df = pd.DataFrame(rows)
    out_df.to_csv(f"{name_col}_clusters.csv", index=False)


Clusters for ConsigneeName:
Canonical: Louis M Gerson Co. Inc
Group: ['Louis M Gerson Co. Inc']

Canonical: Watts Regulator Company
Group: ['Watts Regulator Company']

Canonical: Hollingsworth And Vose Co.
Group: ['Hollingsworth And Vose Co.']

Canonical: Franklin Tape Technical Papers
Group: ['Franklin Tape Technical Papers']

Canonical: Symmons
Group: ['Symmons']

Canonical: Reed And Barton
Group: ['Reed And Barton']

Canonical: Standard Duplicating Machines
Group: ['Standard Duplicating Machines']

Canonical: Tannin Corporation
Group: ['Tannin Corporation']

Canonical: Bay State Specialty Co.
Group: ['Bay State Specialty Co.']

Canonical: Tape O Corp.
Group: ['Tape O Corp.']

Canonical: Ms Walker
Group: ['Ms Walker']

Canonical: Polyone Distribution
Group: ['Polyone Distribution']

Canonical: The Haartz Corporation
Group: ['The Haartz Corporation']

Canonical: Rogers Foam Corp.
Group: ['Rogers Foam Corp.']

Canonical: Bandwagon Inc.
Group: ['Bandwagon Inc.']

Canonical: Micro Mech
